In [103]:
import time
import pyvisa
import lecroy
import numpy as np
import sigilent as rsa
from scipy import signal
from toptica.lasersdk.client import Client, NetworkConnection
import plotly.graph_objs as go
import plotly.offline as pyo

DLCPRO_CONNECTION = '10.225.57.15'

ctr_oscilloscope = 0

def shotnoise(mV, elnoise):
    shotInDecimal = 0.20437407 * mV + -0.9386
    rfShot = 10 * np.log10(shotInDecimal / 1e8 + 10 ** (elnoise / 10))
    return rfShot

%% Helper functions
def decode_file_bin(filename):
    times, power = lecroy.read_timetrace(filename)
    return times, power, filename

def get_wf_ascii(lc, wf='C2'):   # Get short data, good for short files
    lc.write("COMM_HEADER OFF")
    data = lc.query(wf + ':INSP? \"SIMPLE\"')
    nums = np.array(data.strip().split()[1:-1], dtype=float)
    return nums

def get_wf_binary(lc, wf='C2', folder='2023_10_30_osctest', fname_suffix=''): # Use for long data files to make acq faster
    global ctr_oscilloscope
    lc.write(wf + ":WF?")
    wavebin = lc.read_raw()
    ctr_oscilloscope += 1
    filename = folder + '/waveA_%03d_' % ctr_oscilloscope + str(time.monotonic()).replace('.', "_") + wf + fname_suffix + '.trc'
    with open(filename, 'wb') as f:
        f.write(wavebin)
    times, power = lecroy.read_timetrace(filename)
    return times, power, filename


def plot_data(mean_values, std_values, time_values, start_voltage, amplitude, frequency):
    # Calculate time offsets from the start time
    time_offsets = [t - time_values[0] for t in time_values]
    t_piezo = np.linspace(0, 10, 10000)
    
    piezo_voltages = start_voltage + amplitude * signal.sawtooth(2 * np.pi * 1 * np.array(t_piezo), 0.5)
    
    # Create trace with error bars
    mean_trace_with_error_bars = go.Scatter(
        x=time_offsets,
        y=mean_values,
        mode='lines+markers',
        name='Mean'
    )
    
    # Create trace for the laser piezo voltage
    piezo_trace = go.Scatter(
        x=t_piezo,
        y=piezo_voltages,
        mode='lines',
        name='Laser Piezo Voltage',
        yaxis='y2'  # Specify the second y-axis
    )
    
    # Create figure
    fig = go.Figure(data=[mean_trace_with_error_bars, piezo_trace],
                    layout=go.Layout(
                        title='Mean and Standard Deviation Over Time with Laser Piezo Voltage',
                        xaxis=dict(title='Time (s)'),
                        yaxis=dict(title='Mean Value'),
                        yaxis2=dict(
                            title='Laser Piezo Voltage',
                            overlaying='y',
                            side='right'
                        ),
                        showlegend=True
                    ))
    
    # Plot the figure in the notebook
    pyo.iplot(fig)

def plot_monitor(times, signal1, signal2):
    # Create traces for signal1 and signal2
    trace1 = go.Scatter(
        x=times,
        y=signal1,
        mode='lines',
        name='Signal 1 (C2)'
    )
    
    trace2 = go.Scatter(
        x=times,
        y=signal2,
        mode='lines',
        name='Signal 2 (C3)'
    )
    
    # Create figure
    fig = go.Figure(data=[trace1, trace2],
                    layout=go.Layout(
                        title='Signal 1 and Signal 2 as a Function of Time',
                        xaxis=dict(title='Time (s)'),
                        yaxis=dict(title='Signal'),
                        showlegend=True
                    ))
    
    # Plot the figure
    pyo.iplot(fig)

def plot_shotNoise(times, shotNoise):
    
    # Create trace for shotNoise
    trace = go.Scatter(
        x=times,
        y=shotNoise,
        mode='lines',
        name='Shot Noise'
    )
    
    # Create figure
    fig = go.Figure(data=[trace],
                    layout=go.Layout(
                        title='Shot Noise as a Function of Time',
                        xaxis=dict(title='Time (s)'),
                        yaxis=dict(title='Shot Noise (dB)'),
                        showlegend=True
                    ))
    
    # Plot the figure
    pyo.iplot(fig)

def main():
    rm = pyvisa.ResourceManager()
    vu = rm.open_resource("USB0::0xF4EC::0x1301::SSA3XNEQ6R0703::INSTR")
    
    # Open connection to oscilloscope
    rm = pyvisa.ResourceManager()
    print(rm.list_resources())
    lc = rm.open_resource(u'GPIB0::5::INSTR') 
    lc.timeout = 3e3
    
    # Initialize communication
    rsa.countinuousOFF(vu)
    rsa.idn(vu)
    VBW = rsa.whatisVBW(vu)
    print("VBW:%.2f [Hz]" % VBW)
    RBW = rsa.whatisRBW(vu)
    print("RBW:%.2f [Hz]" % RBW)

    measuredNoises = []
    std_values = []
    time_values = []

    with Client(NetworkConnection(DLCPRO_CONNECTION)) as client:
        print("=== Connected Device ===")
        print("This is a {} with serial number {}.\n".format(
            client.get('system-type'), client.get('serial-number')))
        
        start_voltage = client.get('laser1:scan:start')
        amplitude = 0.25
        frequency = 15

        client.set('laser1:scan:amplitude', amplitude)
        client.set('laser1:scan:enabled', True)

        script_start_time = time.perf_counter()

        while time.perf_counter() - script_start_time < 10:
            loop_start_time = time.perf_counter() 
            
            trace, mean, std = rsa.entiretrace(vu, meanstd=True)
            current_time = time.perf_counter()
            measuredNoises.append(mean)
            std_values.append(std)
            time_values.append(current_time)
            elapsed_time = time.perf_counter() - loop_start_time
            remaining_time = 1 / (frequency) - elapsed_time
            time.sleep(max(remaining_time, 0))

        client.set('laser1:scan:enabled', False)
    lc.write('stop')
    folder = r"C:\Users\yshen110\Documents\LabEquip\Toptica\TopticaTest\raw"
    suffix = '_test' # Put any notes for current dataset acq, to go into filename
    times, mV1, filename1 = get_wf_binary(lc, 'C2', folder, 'Monitor1'+suffix)
    times, mV2, filename2 = get_wf_binary(lc, 'C3', folder, 'Monitor2'+suffix)
    
    # Data Post Processing
    elnoise = -67.845880909090910
    # Adjust times so the smallest value is 0
    times = np.array(times)
    times -= np.min(times)
    
    shotNoise = max(shotnoise(mV1, elnoise), shotnoise(mV2, elnoise))
    
    vu.close()
    
    return measuredNoises, std_values, time_values, start_voltage, amplitude, frequency, times, mV1, mV2, shotNoise

mean_values, std_values, time_values, start_voltage, amplitude, frequency, times, mV1, mV2, shotNoise = main()

plot_data(mean_values, std_values, time_values, start_voltage, amplitude, frequency)
plot_monitor(times, mV1, mV2)
plot_shotNoise(times, shotNoise)


('USB0::0xF4EC::0x1301::SSA3XNEQ6R0703::INSTR', 'ASRL1::INSTR', 'ASRL3::INSTR', 'GPIB0::1::INSTR', 'GPIB0::5::INSTR')
Siglent Technologies,SSA3021X,SSA3XNEQ6R0703,2.1.1.3R1

VBW:100.00 [Hz]
RBW:30000.00 [Hz]
=== Connected Device ===
This is a DLCpro with serial number DLC PRO_50319.

